In [2]:
import pickle, collections

In [5]:
snap = pickle.load(open("../memory_dump/oom_3.pickle", "rb"))

In [6]:
import pickle, collections

cnt, total = collections.Counter(), 0
for blk in snap.get("traces", []):  # 新版键名
    sz = blk.get("size", 0)
    if sz <= 0:
        continue
    total += sz
    frames = blk.get("frames", [])
    if frames:
        loc = f"{frames[-1]['filename']}:{frames[-1]['line']}"
        cnt[loc] += sz
print(">>> 总临时分配 %.2f GB" % (total / 1024**3))
for loc, gb in cnt.most_common(10):
    print("%.2f GB  %s" % (gb / 1024**3, loc))

>>> 总临时分配 0.00 GB


In [8]:
snap


{'segments': [{'device': 0,
   'address': 140159781699584,
   'total_size': 20971520,
   'allocated_size': 0,
   'active_size': 0,
   'requested_size': 0,
   'stream': 0,
   'segment_type': 'large',
   'segment_pool_id': (0, 0),
   'is_expandable': False,
   'blocks': [{'address': 140159781699584,
     'size': 20971520,
     'requested_size': 19922944,
     'state': 'inactive',
     'frames': []}],
   'frames': [{'name': '_area_weights_from_masks',
     'filename': '/bd_byta6000i0/users/surgicaldinov2/kyyang/sam2-video-training/sam2_video/utils/masks.py',
     'line': 98},
    {'name': 'merge_object_results_to_category',
     'filename': '/bd_byta6000i0/users/surgicaldinov2/kyyang/sam2-video-training/sam2_video/utils/masks.py',
     'line': 160},
    {'name': 'catch_wrapper',
     'filename': '/bd_byta6000i0/users/surgicaldinov2/miniforge3/envs/sam2/lib/python3.12/site-packages/loguru/_logger.py',
     'line': 1297},
    {'name': 'forward',
     'filename': '/bd_byta6000i0/users/surgic

In [20]:
cnt, total = collections.Counter(), 0
for rec in snap["device_traces"][0]:  # ★ 用 device_traces
    if rec.get("action") != "alloc":
        continue
    sz = rec.get("size", 0)
    total += sz
    frames = rec.get("frames", [])
    if not frames:
        continue
    loc = f"{frames[-1]['filename']}:{frames[-1]['line']}"
    cnt[loc] += sz
print(">>> 总 alloc %.2f GB" % (total / 1024**3))
for loc, gb in cnt.most_common(10):
    print("%.2f GB  %s" % (gb / 1024**3, loc))

>>> 总 alloc 191.01 GB
57.50 GB  /bd_byta6000i0/users/surgicaldinov2/kyyang/sam2-video-training/train.py:234


In [19]:
len(snap["device_traces"][0])

100000

In [21]:
import pickle, torch
from collections import defaultdict

In [25]:
buckets = defaultdict(lambda: {"num": 0, "bytes": 0})

for seg in snap["segments"]:
    for blk in seg["blocks"]:
        if blk.get("state") != "active_allocated":
            continue
        # 用最后 3 帧当 key
        key = "\n".join(
            f"{f['filename']}:{f['line']}:{f['name']}" for f in seg["frames"][-3:]
        )
        buckets[key]["num"] += 1
        buckets[key]["bytes"] += blk["size"]

# 按总字节倒序
for key, v in sorted(buckets.items(), key=lambda kv: kv[1]["bytes"], reverse=True)[:20]:
    print(f"{v['num']:>6} 块 | {v['bytes'] / 1024 / 1024:>8.2f} MB | {key}")

   697 块 |   297.84 MB | 
     1 块 |    64.00 MB | /bd_byta6000i0/users/surgicaldinov2/miniforge3/envs/sam2/lib/python3.12/site-packages/hydra/_internal/utils.py:394:_run_hydra
/bd_byta6000i0/users/surgicaldinov2/miniforge3/envs/sam2/lib/python3.12/site-packages/hydra/main.py:94:decorated_main
/bd_byta6000i0/users/surgicaldinov2/kyyang/sam2-video-training/train.py:234:<module>


In [24]:
import pprint

print("top keys :", list(snap.keys()))

# 2. 随便拉一条 segment 看内部字段
if "segments" in snap and len(snap["segments"]):
    pprint.pprint(snap["segments"][0])  # 把第一条完整结构打出来
else:
    pprint.pprint(snap)  # 如果没有 segments，直接看整

top keys : ['segments', 'device_traces', 'allocator_settings', 'external_annotations']
{'active_size': 0,
 'address': 140159781699584,
 'allocated_size': 0,
 'blocks': [{'address': 140159781699584,
             'frames': [],
             'requested_size': 19922944,
             'size': 20971520,
             'state': 'inactive'}],
 'device': 0,
 'frames': [{'filename': '/bd_byta6000i0/users/surgicaldinov2/kyyang/sam2-video-training/sam2_video/utils/masks.py',
             'line': 98,
             'name': '_area_weights_from_masks'},
            {'filename': '/bd_byta6000i0/users/surgicaldinov2/kyyang/sam2-video-training/sam2_video/utils/masks.py',
             'line': 160,
             'name': 'merge_object_results_to_category'},
            {'filename': '/bd_byta6000i0/users/surgicaldinov2/miniforge3/envs/sam2/lib/python3.12/site-packages/loguru/_logger.py',
             'line': 1297,
             'name': 'catch_wrapper'},
            {'filename': '/bd_byta6000i0/users/surgicaldinov2/